This Jupyter notebook will use the SEAScope viewer and SEAScope Python bindings to retrieve inputs data 
* author: Lucile Gaultier, Ziad El Khoury Hanna, OceanDataLab
* date: 2022-11-12

To install SEAScope, follow the instructions on the [SEAScope website](https://seascope.oceandatalab.com/) and demonstrated in our ["SEAScope How To" YouTube playlist](https://www.youtube.com/playlist?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK).

To install the required Python packages, follow the instructions on https://pypi.org/project/SEAScope-env-OTC2023.
* **Windows** users can also follow the [Complete SEAScope install with Python modules for OTC23 on Windows](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=132s) video on YouTube
* **macOS** users can also follow the [Installing SEAScope Python modules for OTC23 on macOS](https://youtu.be/w5f0ow6iPOY?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=6) video on YouTube

# Compare ocean surface current structures with SST fronts

Ocean tracers such as the SST or Chlorophyll-a are advected by the current and provide us with a different view of the ocean surface dynamics.\
These medium to high resolution images from remote sensing observation can be used to validate the position of the dynamical structures in an ocean surface velocity product.\
From a tracer image, we can retrieve frontal structures and compute the flux crossing a front.

Let’s call $\vec{v}[P]$, the velocity vector of the currents product at a point $P$, and a front formed by $P_i\begin{bmatrix}lon_i\\ lat_i\end{bmatrix}$ points.\
For each point $P_i$, we compute the flow across the front:

$$Flow[P_i] = \frac{\left|{\vec{v}[P_i]}\cdot\vec{\delta_i}\right|}{\left|\vec{v}[P_i]\right| \left|\vec{\delta_i}\right|}$$

with $\vec{\delta_i}\begin{bmatrix}lat_{i+1} - lat_{i-1}\\ (lon_{i-1} - lon_{i+1}) cos(lat_i)\end{bmatrix}$ the perpendicular to the $i$<sup>th</sup> segment of the front in the [equirectangular projection](https://en.wikipedia.org/wiki/Equirectangular_projection).

The smaller the flow, the more accurate is the velocity as we assume here that the velocity is transporting the tracer and thus the velocity and the fronts should be aligned in most cases.

In this notebook, we will use three different velocity products:
* The CMEMS GlobCurrent geostrophic current
* The BFN QG (WOC) current
* The CMEMS Mercator 1/12 model current

This notebook will teach you how to:
* Import data from SEAScope
* Export data to SEAScope
* Evaluate the performance of different velocity products using SST frontal structures

<div class="alert alert-warning">

**This notebook uses the following data collection:**

* directory: `cmems_008_046`, label: `CMEMS sea level NRT observations`
* directory: `cmems_001_030`, label: `CMEMS Mercator DT 1/12`
* directory: `woc-bfnqg-3h`, label: `WOC BFN QG current`
* directory: `seviri`, label: `SEVIRI SST` (optional, used at the end for visual analysis and comparison using the viewer)

Check that you have them in your SEAScope catalogue before continuing with this notebook.\
If not, you can download an archive containing them at https://ftp.odl.bzh/odl/events/otc23/data_ila13.zip.

To learn how to add data to SEAScope, you can watch one of the following YouTube videos:
* [How to add data to SEAScope on **Windows**](https://youtu.be/TsJSg7V7WNU?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=2)
    * or the "Add data to SEAScope" chapter of [How to add data to SEAScope on **Windows**](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=40s)
* [How to add data to SEAScope on **macOS**](https://youtu.be/s5X3ewpmcuw?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=5)
* [How to add data to SEAScope on **Linux**](https://youtu.be/3ZAzgl3v2lo?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=8)

</div>

In [ ]:
# Import necessary modules
%matplotlib inline
import matplotlib.pyplot as plt
import numpy
import contextlib
import os
import datetime
import json
import urllib
import urllib.request
from pathlib import Path
from scipy.spatial import KDTree


@contextlib.contextmanager
def open_file_at(location):
    is_file = (
        isinstance(location, Path)
        or urllib.parse.urlparse(location).scheme in ('', 'file')
    )
    if is_file:
        with open(location, 'rt', encoding='utf-8') as file:
            yield file
    else:
        with urllib.request.urlopen(location) as response:
            yield response


# Create once the collection for this notebook
collection_by_name = {}
collection_id = None
collection = None
import SEAScope.lib.utils
SEAScope.lib.utils.init_ids(20, 2000)

## 1. Define functions that will be used to compute the flows across fronts

Define a 1d smoothing function to smooth the input fronts

In [ ]:
def smooth(x, window_size=5, window='hanning'):
    _ = int(window_size)
    assert window_size == _ and _ > 0 and _ % 2 == 1, "smoothing window size must be an odd integer > 0"
    window_size = _

    if window_size < 3:
        return x

    if window == 'flat':  # moving average
        window = 'ones'
    w = getattr(numpy, window)(window_size)

    # Extend the input array x by mirroring the edges
    m = int(window_size / 2)
    s = numpy.r_[x[m:0:-1], x, x[-2:-m-2:-1]]

    # Compute the smoothed output by convolving the window with the extended input.
    # The output will have the same length as the original input
    y = numpy.convolve(w / w.sum(), s, mode='valid')

    return y

Compare fronts and velocity:
* Interpolate the velocity onto the front point
* Compute direction of the front
* Compute the flow across a front (dot product between the perpendicular to a front and a velocity vector)

In [ ]:
def prepare_fronts(fronts_dict):
    fronts = []
    fronts_count = len(fronts_dict['lon'])
    for i in range(fronts_count):
        if len(fronts_dict['lon'][i]) < 2:
            # Not enough points
            continue

        front_lon = numpy.array(fronts_dict['lon'][i], dtype='float64')
        front_lat = numpy.array(fronts_dict['lat'][i], dtype='float64')
        front_sst_grad_lon = numpy.array(fronts_dict['sst_grad_lon'][i], dtype='float64')
        front_sst_grad_lat = numpy.array(fronts_dict['sst_grad_lat'][i], dtype='float64')

        # Smooth the front
        front_lon = smooth(front_lon)
        front_lat = smooth(front_lat)
        front_sst_grad_lon = smooth(front_sst_grad_lon)
        front_sst_grad_lat = smooth(front_sst_grad_lat)

        # Compute the front direction at each point intermediate of the front
        delta_lon = front_lon[2:] - front_lon[:-2]
        delta_lat = front_lat[2:] - front_lat[:-2]

        # Project delta_lon using an equirectangular projection
        delta_lon *= numpy.cos(numpy.deg2rad(front_lat[1:-1]))

        # Compute the normalized perpendicular vector to the front
        delta_norm = numpy.sqrt(delta_lon ** 2 + delta_lat ** 2)
        delta_perp = numpy.stack((delta_lat / delta_norm, -delta_lon / delta_norm), axis=-1)

        # Compute the magnitude of the SST gradient at each point of the front
        front_sst_gradient = numpy.sqrt(front_sst_grad_lon ** 2 + front_sst_grad_lat ** 2)

        # Add front to the result
        fronts.append({
            'flag': fronts_dict['flag_front'][i],
            'gradient_sst': front_sst_gradient,
            'lon': front_lon,
            'lat': front_lat,
            'delta_perp': delta_perp,
        })

    return fronts

def velocity_across_fronts(fronts, velocity_dict, gradient_threshold=0.05):
    points = list(zip(velocity_dict['lat'].ravel(), velocity_dict['lon'].ravel()))
    uv_tree = KDTree(points, leafsize=10)
    uflat = velocity_dict['u'].flatten()
    vflat = velocity_dict['v'].flatten()

    flows = []
    for front in fronts:
        front_lon = front['lon']
        front_lat = front['lat']
    
        # Find the nearest velocity vector (u, v) at each intermediate point of the front
        _, inds = uv_tree.query(list(zip(front_lat[1:-1], front_lon[1:-1])), k=1)
        u = uflat[inds]
        v = vflat[inds]

        # Remove erroneous velocities
        u[numpy.absolute(u) > 100] = numpy.nan
        v[numpy.absolute(v) > 100] = numpy.nan

        # Compute normalized velocity vector
        vel_norm = numpy.sqrt(u ** 2 + v ** 2)
        vel = numpy.stack((u / vel_norm, v / vel_norm), axis=-1)

        # Compute the dot product between the perpendicular to the front and
        # the velocity vector at each intermediate point of the front
        dot = numpy.sum(vel * front['delta_perp'], axis=-1)

        # Compute the flow across the front at each intermediate point of the front
        flow = numpy.absolute(dot)

        # Pad the flow array with NaNs to maintain same size as the input points
        flow = numpy.r_[numpy.nan, numpy.absolute(dot), numpy.nan]

        # Replace flow values with NaN where the SST gradient is under the given threshold
        flow[front['gradient_sst'] <= gradient_threshold] = numpy.nan

        # Add flow to the result
        flows.append({
            'front': front,
            'velocity': velocity_dict,
            'flux_across': flow,
        })

    return flows

## 2. Load fronts


This notebook uses fronts derived from hourly SEVIRI SST observation.

Load json file into a dictionary to retrieve the front position, flags and sst gradient.

In [ ]:
# ⚠️ You can adapt the path/URL to the file if necessary
file = 'https://ftp.odl.bzh/odl/events/otc23/seviri_sst_20190925T170000.json'
# file = '/tmp/seviri_sst_20190925T170000.json'

with open_file_at(file) as response:
    fronts_dict = json.load(response)

# Convert start and stop time of the data into datetime
fstart = datetime.datetime.strptime(fronts_dict['time_coverage_start'], '%Y%m%dT%H%M%SZ')
fstop = datetime.datetime.strptime(fronts_dict['time_coverage_end'], '%Y%m%dT%H%M%SZ')

fronts = prepare_fronts(fronts_dict)
print(f'Loaded {len(fronts)} fronts between {fstart} and {fstop}')

## 3. Find the data of interest in SEAScope

##### Select and locate the data in the SEAScope viewer

1. In the "Catalogue" (the panel on the right), select one or more of the following:
    * collection `CMEMS sea level NRT observations`, variable `geostrophic current from MADT`
    * collection `CMEMS Mercator DT 1/12`, variable `current`
    * collection `WOC BFN QG current`, variable `current`
2. Go to the date where you have the fronts (highlighted in green in the timeline)
    * The 25<sup>th</sup> of September 2019 at 17:00:00
3. Zoom into the Agulhas region (where the fronts have been computed)

## 3. Get data from the SEAScope viewer using the python bindings

##### Extract the data from SEAScope

1. Zoom-in to properly see the structures in the data, but not too much so that you still see the whole Agulhas region (the resolution of the extraction depends on the zoom level)
2. Draw a polygon over the region you want to extract:
    1. Start drawing by clicking on the 3<sup>rd</sup> button to the right of the pen icon in the toolbar or by hitting the <kbd>P</kbd> key
    2. Place the corners of the polygon by left-clicking on the globe
    3. Once all the corners placed, hit the <kbd>Enter</kbd> or <kbd>Return</kbd> key to commit your polygon
3. Select the polygon you just created by clicking on it
4. Extract the data intersecting that polygon by clicking on the extract button in the "Selected annotation" panel

You can also watch the [How to export data from SEAScope](https://youtu.be/jN-67nwWbUA) video on YouTube.

Load the extracted data

In [ ]:
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()

Identify current granules among the extracted data

In [ ]:
velocity_granules = []

for k, (granule_path, granule_info) in enumerate(extractions.items()):
    granule_name = os.path.basename(granule_path)

    # Print extracted granule data 
    print(f'{k} - {granule_name}')
    print('\n'.join([f'\t{_}' for _ in granule_info['data']]))

    if 'phy_l4' in granule_name:
        name_vel = 'GlobCurrent'
        u = granule_info['data']['ugos']
        v = granule_info['data']['vgos']
    elif 'mercator' in granule_name:
        name_vel = 'Mercator'
        u = granule_info['data']['uo']
        v = granule_info['data']['vo']
    elif 'bfnqg' in granule_name:
        name_vel = 'BFNQG'
        u = granule_info['data']['ug']
        v = granule_info['data']['vg']
    else:
        continue

    velocity_granules.append({
        'granule_info': granule_info,
        'name': name_vel,
        'u': u,
        'v': v,
    })

if len(velocity_granules) == 0:
    print('Wrong collections selected, go back to SEAScope and select at least one of the following:')
    print('* "CMEMS sea level NRT observations" collection, "geostrophic current from MADT" variable')
    print('* "CMEMS Mercator DT 1/12" collection, "current" variable')
    print('* "WOC BFN QG current" collection, "current" variable')
    print()
    raise Exception('See issues above')

# Make sure the result is reset
granule_id = None

## 4. Compute the flows crossing fronts

In [ ]:
from SEAScope.lib.utils import get_lonlat

results = []
for velocity_granule in velocity_granules:
    granule_info = velocity_granule['granule_info']
    start = granule_info['meta']['start']
    stop = granule_info['meta']['stop']

    if fstart > stop or fstop < start:
        print('No time overlap between fronts and velocity field coverages')
        print(f'Fronts coverage starts on {fstart} and ends on {fstop}')
        print(f'Velocity coverage starts on {start} and ends on {stop}')
        continue

    # Get coordinates, data and time coverage of the extracted granules
    lon, lat = get_lonlat(granule_info, velocity_granule['u'].shape)

    u = velocity_granule['u']
    v = velocity_granule['v']
    u[u.mask] = 0
    v[v.mask] = 0

    velocity_dict = {
        'u': u,
        'v': v,
        'lat': lat,
        'lon': lon,
    }
    flows = velocity_across_fronts(fronts, velocity_dict, gradient_threshold=0.0)
    results.append({
        'name': velocity_granule['name'],
        'flows': flows,
        'velocity': velocity_dict,
        'time_coverage_start': start,
        'time_coverage_end': stop,
    })

## 5. Plot the results

Plot the velocity norm, vectorfield and the flow computed on frontal structure

In [ ]:
result = results[0]
velocity = result['velocity']
flows = result['flows']

fig = plt.figure(figsize=(16,10))
plt.pcolormesh(velocity['lon'], velocity['lat'],
               numpy.sqrt(velocity['u']**2 + velocity['v']**2),
               cmap='jet', vmin=0, vmax=2)

X, Y = numpy.meshgrid(numpy.arange(0, velocity['u'].shape[1]),
                      numpy.arange(0, velocity['u'].shape[0]))
ss = 15
Q = plt.quiver(velocity['lon'][::ss, ::ss], velocity['lat'][::ss, ::ss],
               numpy.clip(velocity['u'][::ss,::ss],-2,2),
               numpy.clip(velocity['v'][::ss,::ss],-2,2))
qk = plt.quiverkey(Q, 0.5, 0.98, 2, r'$2 \frac{m}{s}$', labelpos='W',
                   fontproperties={'weight': 'bold'})
for flow in flows:
    front = flow['front']
    flux_across = flow['flux_across']
    plt.scatter(front['lon'], front['lat'], c=flux_across)

cbar=plt.colorbar()

## 6. Export flows back to SEAScope

In [ ]:
from SEAScope.lib.utils import create_collection, create_variable
from SEAScope.lib.utils import create_granule, set_field

**Define Collection**

A granule has to belong to a collection\
**<span style="color:red">You may choose a name for the collection `collection_name`</span>**

In [ ]:
# ⚠️ You can choose the quality level of front you want export
# flag varies from 1 to 6, 1 being the 16.67% fronts the more reliable,
# and 6 the 16.67% fronts the less reliable. 
# quality of fronts bigger than 4 are generally not relevant for automatic current validation
max_flag = 3

# ⚠️ You can choose your collection name
collection_name = f'Flows for flag<={max_flag}'

if collection_name in collection_by_name:
    # Reuse existing collection
    collection_id, collection = collection_by_name[collection_name]
else:
    # Create new collection
    collection_id, collection = create_collection(collection_name)
    collection_by_name[collection_name] = (collection_id, collection)

print(collection_id)

**Define the granules that will hold the results**\
Granules are defined by their spatial and temporal coverage.

In [ ]:
granules = []

for front in fronts:
    if f'granule_{collection_id}' in front:
        continue

    if front['flag'] > max_flag:
        continue

    # Spatial coverage
    # Each position of the trajectory will be used as GCP
    gcps = []
    for i in range(len(front['lon'])):
        gcps.append({
            'lon': front['lon'][i],
            'lat': front['lat'][i],
            'i': i,
            'j': 0,
        })

    # Create granule
    granule_id, granule = create_granule(collection_id, gcps, fstart, fstop)

    # Save the granule on it's front
    front[f'granule_{collection_id}'] = granule

    # Add granule to list
    granules.append(granule)

**A granule will contain each result matrix as what we call a "field".\
<span style="color:red">You may choose a name for the field `field_name`</span>\
Next you need to tell SEAScope what to display: this is done by defining a "variable" which can be composed of
one, two or three fields.\
When a variable has two fields, these are considered to be the meridional and zonal components of a vector field.\
<span style="color:red"> You may choose a name for each variable you want to display `variable_name`</span>**

In [ ]:
variables = []
# Initial zindex to set up the order of layers of the different variables in SEAScope
_zini = 0.923

for result in results:
    # ⚠️ You can choose your field name
    field_name = f'flux_across_{result["name"]}'

    # ⚠️ You can choose your label name
    variable_name = f'flux across {result["name"]}'

    # Attach data field to the granules
    flows = result['flows']
    for flow in flows:
        front = flow['front']
        granule = front.get(f'granule_{collection_id}')
        if granule:
            set_field(granule, field_name, flow['flux_across']*2)

    # Create a variable for each velocity
    variable = create_variable(collection, variable_name, [field_name], dims=1)
    if variable:
        # Set rendering configuration
        rcfg = variable['rendering']
        rcfg['min'] = 0.34 
        rcfg['max'] = 0.77
        rcfg['colormap'] = 'doppler'
        rcfg['opacity'] = 1
        rcfg['zindex'] = _zini
        _zini = min(_zini + 0.1, 1.)
        # Add variable to list
        variables.append(variable)

**Finally, send the collection, granule and variable to SEAScope**

In [ ]:
hostname = '127.0.0.1'
port = 11155
with SEAScope.upload.connect(hostname, port) as link:
    # Upload the collection first (remember: a granule cannot exist before its collection has been uploaded!)
    SEAScope.upload.collection(link, collection)

    # Then the granules
    for granule in granules:
        SEAScope.upload.granule(link, granule)

    # Now SEAscope has access to the data, all that remains is telling the application what and how it should display them, by uploading the variable definition
    for variable in variables:
        SEAScope.upload.variable(link, variable)

## 7. Visualize your flux in the SEAScope viewer

Your new collection should have appeared in the "Catalogue"
* Your collection is the `collection_name` you have defined previously
* Your variables are the `variable_name` you have defined previously, you should have as many variables as current you have extracted
* Select the data you have just exported

In the "Catalogue" (the panel on the right), select the current streamlines and SEVIRI SST:
* collection `CMEMS sea level NRT observations`, variable `geostrophic current from MADT (streamlines)`
* collection `CMEMS Mercator DT 1/12`, variable `current (streamlines)`
* collection `WOC BFN QG current`, variable `current (streamlines)`
* collection `SEVIRI SST`, variable `sea_surface_temperature`

Compare the direction of the streamlines with the direction of the front, the flux across the current should be high if the directions are very different and small if the directions are similar.\
Compare the flux across the current in different areas and check which current performs best in the different regions of your polygon.
Compare also the flux and streamlines with the fronts and eddies visible in the SEVIRI SST.